<h1 align=center><font size = 6>Identifying Fast Food Franchise Restaurants in Houston, Texas to Pursue for Purchase</font></h1>

### **Applied Data Science Capstone Project by Joe McReynolds**

The goal of the project is to identify poorly rated fast-food, franchise restaurants that are the best canditates to purchase and turn around to profitability. A work flow utilizing Foursquare data will be designed and executed. The results will be reported with emphasis on visual displays.

### **TABLE OF CONTENTS**

1. Introduction / Business Problem
2. Data  
3. Methodology   
4. Analysis  
5. Conclusion  

### **INTRODUCTION / BUSINESS PROBLEM**

The business problem is identifying distressed or underperforming “fast food” franchise restaurants in Houston, Texas for restaurant investors to purchase and turn around to profitability. The plan is to leverage Foursquare location data to design a work flow that helps commercial real estate investors locate “fast food” franchise restaurants to purchase for investment.

1. Underperforming or poorly rated restaurants will be located. The focus is on poorly rated restaurants because they are likely to cost less to purchase than high performing properties and be available.

2. From that low performing group, restaurants that have the most promise of becoming higher rated, profitable properties for the investor will identified by evaluating how that specific franchise typically performs in the type of neighborhood in which it is located in Houston. The Foursquare data service is well suited for this task because it not only locates the properties but also contains venue statistics and ratings for each restaurant.

The value of the project is to give investors another piece of evidence to add to their decision process and should improve their chance of buying the underperforming business that will become profitable.

### **DATA**

Two main data sources will be used in the project. FourSquare data will be combined with local Houston neighborhood data found in web research to complete the project .

### Houston Neighborhood area data 

The Houston neighborhood data will be used to segment Houston into areas that through cluster analysis will be grouped into neighborhoods with similar venues found in the Foursquare data. 

Information on Houston neighborhoods is located at the following web page:
https://en.wikipedia.org/wiki/List_of_Houston_neighborhoods

The necessary neighborhood info will be scraped from this web page, and latitude longitude will be generated using geocoder packages imported from the geopy library.

#### 88 "super" neighborhoods exist in the Houston area.
Those neighborhoods or some subset, if time runs short, will be used as the neighborhood groupings for this analysis.

<img src = "https://upload.wikimedia.org/wikipedia/commons/thumb/c/c2/Houston_superneighborhoods.png/1000px-Houston_superneighborhoods.png" width = 800, align = "center" alt="logistic regression block diagram" />

### Foursquare Venue data 

Foursquare data will used in multiple parts of the workflow. Specifically two data types will be utilized from Foursquare, general Venue category data and Venue specific rating data.

1) General Venue category data will be gathered for each neighborhood in preparation for cluster analysis to group similar neighboroods.

2) Venue specific rating data will be used after cluster analysis to analysize the performance of individual fast food restaurants.  

The Foursquare data service is well suited for this task because it not only locates the properties but also contains venue statistics and ratings for each restaurant. 

### **METHODOLOGY**

The workflow to identifying underperforming “fast food” franchise restaurants in Houston, Texas for restaurant investors to purchase is a four part process.

1) Neighborhood Polygon Preparation

Houston Neighborhood areas were downloaded as shapefiles from City of Houston. First they were transformed to json format to plot areas on folium maps for viewing results. Second, centroid points for each neighorhood polygon were needed to use foursquare explore api because it functions best searching around a latitude longitude point. 
    
2) General Venue Category Neighborhood Comparison 
    
The neighborhoods were compared based on the types of venue categories and those categories prevalence in each neighborhood. Foursquare data is downloaded preprocessed and run through a cluster analysis to group neighborhoods with similar venue category composition.
    
3) Fast Food Restaurant Franchise Neighborhood Comparison
    
As well as comparing general category composition, neighborhoods were compared based on the fast food franchise composition and prevalence. Foursquare data was further filtered down to a set of common fast food franchises and run through another cluster analysis to again group similar neighborhoods for comparison.
    
4) Fast Food Restaurant Rating analysis
    
Finally, a small subset of similar neighborhoods based the previous anlysis was selected for rating    comparison. Foursquare ratings data are part of their premium service and our free service limits the amount of requests that can be made on this data. Ideally, I would have done all neighborhoods.
    
With neighborhood's venues filtered to only fast food restaurants, the venue id for each individual   restaurant was submitted to the Foursquare API for detailed information that includes ratings and how many likes customers had given a venue. Results were sorted by neighborhood and printed to search for restaurants in comparible neighborhoods that are lower rated compared to similar restaurants. Results were also sorted by fast food franchise and printed to search for restaurants in among the same franchise venues that had an anomalously low ratings.
    
Identifying these lower rated restaurants would allow the investor to build a list a restaurants to begin looking into further to pursue for purchase.
        

### **ANALYSIS**

### **PART 1 Neighborhood Polygon Preprocessing**

### First libraries need to be set up and imported

In [38]:
import requests # library to handle requests
import pandas as pd # library for data analsysis
import numpy as np # library to handle data in a vectorized manner
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
from geopy.geocoders import Nominatim # module to convert an address into latitude and longitude values

# libraries for displaying images
from IPython.display import Image 
from IPython.core.display import HTML 

import json # library to handle JSON files
# tranforming json file into a pandas dataframe library
from pandas.io.json import json_normalize

# import k-means from clustering stage
from sklearn.cluster import KMeans

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt
#%matplotlib inline 

#!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library

print('Folium installed')
print('Libraries imported.')

Folium installed
Libraries imported.


In [39]:
#Run only if converting
from osgeo import ogr, osr, gdal
import ogr2ogr 
print('Libraries imported for shapefile conversion.')

Libraries imported for shapefile conversion.


In [40]:
#Only needed to build the file one time -- comment out thereafter
#!ogr2ogr -f GeoJSON -t_srs EPSG:4326 houstonnbhoods1.json COH_SUPER_NEIGHBORHOODS.shp

### Create houston neighborhood list with lat longs from polygon centroids

In [41]:
# Import necessary modules
#import pandas as pd
import random
import geopandas as gpd
print('Libraries imported.')

Libraries imported.


In [42]:
# Set filepath (fix path relative to yours)
fp = r'C:\Users\Joe\JoeJupytrNbks\COH_SUPER_NEIGHBORHOODS.shp'

In [43]:
# Read file using gpd.read_file()
gdf = gpd.read_file(fp)

In [44]:
type(gdf)

geopandas.geodataframe.GeoDataFrame

In [55]:
gdf.head(88)

OBJECTID   PERIMETER  POLYID                                      SNBNAME  \
0          1   16572.025      60                                  FOURTH WARD   
1          2   43118.770      63                                  SECOND WARD   
2          3   39256.388      61                                     DOWNTOWN   
3          4   59784.698      59                   CLINTON PARK TRI-COMMUNITY   
4          5   75759.390      21                               GREATER UPTOWN   
5          6  113669.041       5                               GREATER INWOOD   
6          7     637.881      78                           GREATER HOBBY AREA   
7          8   60053.707      73              GOLFCREST / BELLFORT / REVEILLE   
8         10  212370.594      17                         ELDRIDGE / WEST OAKS   
9         11   88194.439      22  WASHINGTON AVENUE COALITION / MEMORIAL PARK   
10        12   55192.156      55                           GREATER FIFTH WARD   
11        13   80879.515      56                 DENVER HARBOR / PORT HOUSTON   
12        14   47322.950      57                           PLEASANTVILLE AREA   
13        15  110804.437      58                                   NORTHSHORE   
14        16   47186.948      14                      LAZYBROOK / TIMBERGROVE   
15        17   67130.734      15                              GREATER HEIGHTS   
16        18   52352.042      52                             KASHMERE GARDENS   
17        19   80038.578      77                                     MINNETEX   
18        20   50141.033      51                               NEAR NORTHSIDE   
19        21   57962.346      86                           SPRING BRANCH EAST   
20        23   43303.814      84                          SPRING BRANCH NORTH   
21        24   57859.757      53                    EL DORADO / OATES PRAIRIE   
22        25   57315.513      85                        SPRING BRANCH CENTRAL   
23        26   30493.459      54                                   HUNTERWOOD   
24        27   33779.628      50                                    SETTEGAST   
25        28   33997.809      11                                     LANGWOOD   
26        29   42365.115      13                         INDEPENDENCE HEIGHTS   
27        30   83851.206      12                            CENTRAL NORTHWEST   
28        31   58565.130      48                    TRINITY / HOUSTON GARDENS   
29        32   56176.320       3                                   CARVERDALE   
30        33   71061.565      46                         EASTEX - JENSEN AREA   
31        34   81176.060      49                                 EAST HOUSTON   
32        35   87815.580       6                                   ACRES HOME   
33        36  102420.982      45                          NORTHSIDE/NORTHLINE   
34        37   28102.301       7                                HIDDEN VALLEY   
35        38   83347.430      47                 EAST LITTLE YORK / HOMESTEAD   
36        39   52713.975       1                                  WILLOWBROOK   
37        40  117958.273       2                          GREATER GREENSPOINT   
38        41  170943.477      42                           IAH / AIRPORT AREA   
39        42  198374.308      43                                KINGWOOD AREA   
40        43  429584.145      44                                 LAKE HOUSTON   
41        44   73300.982       4               FAIRBANKS / NORTHWEST CROSSING   
42        45   31832.840       8                                   WESTBRANCH   
43        46   72720.943      26                                   SHARPSTOWN   
44        47   38113.022      29                                     WESTWOOD   
45        49   81085.410      41                            FORT BEND HOUSTON   
46        50   28114.627      39                              FONDREN GARDENS   
47        51  161035.331      80                       SOUTH BELT / ELLINGTON   
48        52   71756.689      76   

In [59]:
gdf["LONG"] = gdf.centroid.x
gdf["LAT"] = gdf.centroid.y

#### Tranform the geopandas data into a *pandas* dataframe

In [74]:
neighborhood_list = pd.DataFrame(gdf[['OBJECTID', 'POLYID', 'SNBNAME', 'Shapearea', 'LAT', 'LONG' ]])

neighborhood_list.rename(columns={'SNBNAME': "Neighborhood"}, inplace=True)
neighborhood_list.head()

OBJECTID  POLYID                Neighborhood     Shapearea        LAT  \
0         1      60                 FOURTH WARD  1.296982e+07  29.757116   
1         2      63                 SECOND WARD  8.040472e+07  29.750962   
2         3      61                    DOWNTOWN  7.550023e+07  29.756689   
3         4      59  CLINTON PARK TRI-COMMUNITY  7.655352e+07  29.748397   
4         5      21              GREATER UPTOWN  2.297921e+08  29.756552   

        LONG  
0 -95.380766  
1 -95.327939  
2 -95.359096  
3 -95.262714  
4 -95.475614

In [75]:
def random_html_color():
    r = random.randint(0,256)
    g = random.randint(0,256)
    b = random.randint(0,256)
    return '#%02x%02x%02x' % (r, g, b)

In [76]:
def style_fcn(x):
        #The style function can return random colors. 
        return { 'fillColor': random_html_color() }

In [164]:

neighborhood_polys = f'houstonnbhoods1.json'

Hmap = folium.Map(
    location=[29.759, -95.367],
    zoom_start=10  # Limited levels of zoom for free Mapbox tiles.
)

folium.GeoJson(
    neighborhood_polys,
    name='geojson',
    style_function=style_fcn,
).add_to(Hmap)


latitudes = list(neighborhood_list.LAT)
longitudes = list(neighborhood_list.LONG)
labels = list(neighborhood_list.Neighborhood)

for lat, lng, label in zip(latitudes, longitudes, labels):
    Hmap.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=1, # define how big you want the circle markers to be
            color='yellow',
            fill=False,
            popup=label
            )
    )
# add pop-up text to each neighborhood on the map
#for lat, lng, label in zip(latitudes, longitudes, labels):
#    folium.Marker([lat, lng], popup=label).add_to(Hmap)    

#Hmap.add_child(folium.LatLngPopup())

folium.LayerControl().add_to(Hmap)

Hmap

In [82]:
neighborhood_list.head(5)

OBJECTID  POLYID                Neighborhood     Shapearea        LAT  \
0         1      60                 FOURTH WARD  1.296982e+07  29.757116   
1         2      63                 SECOND WARD  8.040472e+07  29.750962   
2         3      61                    DOWNTOWN  7.550023e+07  29.756689   
3         4      59  CLINTON PARK TRI-COMMUNITY  7.655352e+07  29.748397   
4         5      21              GREATER UPTOWN  2.297921e+08  29.756552   

        LONG  
0 -95.380766  
1 -95.327939  
2 -95.359096  
3 -95.262714  
4 -95.475614

### **PART 2 General Venue Category Neighborhood Comparison**

### 2A - Define Foursquare Credentials and Version 

##### Need your Foursquare developer account and credentials for PART 2, 3, and 4.

In [83]:
CLIENT_ID = 'TE0PG2YHTFN3QLWZM5ET0O0EGQX1XNEJJECQRZJVWXAG4G10' # your Foursquare ID
CLIENT_SECRET = 'CWPXUWBN55NCV0IBFRH3VPMX4JZM4UOKLXL2VWAZT0HU01FM' # your Foursquare Secret
VERSION = '20180605'
LIMIT = 300
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: TE0PG2YHTFN3QLWZM5ET0O0EGQX1XNEJJECQRZJVWXAG4G10
CLIENT_SECRET:CWPXUWBN55NCV0IBFRH3VPMX4JZM4UOKLXL2VWAZT0HU01FM


#### Let's explore the first neighborhood in our dataframe.

### 2B - Get General Categagories Neighborhoods in Houston

#### Define function to get venue data by looping for all the neighborhoods in Houston

In [84]:
def getNearbyVenues(names, latitudes, longitudes, radius):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Run function to get venue data by looping for all the neighborhoods in Houston and create a new dataframe called *houston_venues*.

In [86]:

houston_venues = getNearbyVenues(names=neighborhood_list['Neighborhood'],
                                   latitudes=neighborhood_list['LAT'],
                                   longitudes=neighborhood_list['LONG'],
                                   radius=2000
                                  )



FOURTH WARD
SECOND WARD
DOWNTOWN
CLINTON PARK TRI-COMMUNITY
GREATER UPTOWN
GREATER INWOOD
GREATER HOBBY AREA
GOLFCREST / BELLFORT / REVEILLE
ELDRIDGE / WEST OAKS
WASHINGTON AVENUE COALITION / MEMORIAL PARK
GREATER FIFTH WARD
DENVER HARBOR / PORT HOUSTON
PLEASANTVILLE AREA
NORTHSHORE
LAZYBROOK / TIMBERGROVE
GREATER HEIGHTS
KASHMERE GARDENS
MINNETEX
NEAR NORTHSIDE
SPRING BRANCH EAST
SPRING BRANCH NORTH
EL DORADO / OATES PRAIRIE
SPRING BRANCH CENTRAL
HUNTERWOOD
SETTEGAST
LANGWOOD
INDEPENDENCE HEIGHTS
CENTRAL NORTHWEST
TRINITY / HOUSTON GARDENS
CARVERDALE
EASTEX - JENSEN AREA
EAST HOUSTON
ACRES HOME
NORTHSIDE/NORTHLINE
HIDDEN VALLEY
EAST LITTLE YORK / HOMESTEAD
WILLOWBROOK
GREATER GREENSPOINT
IAH / AIRPORT AREA
KINGWOOD AREA
LAKE HOUSTON
FAIRBANKS / NORTHWEST CROSSING
WESTBRANCH
SHARPSTOWN
WESTWOOD
FORT BEND HOUSTON
FONDREN GARDENS
SOUTH BELT / ELLINGTON
SOUTH ACRES / CRESTMONT PARK
BRAYS OAKS
CENTRAL SOUTHWEST
SUNNYSIDE
ALIEF
PECAN PARK
CLEAR LAKE
WESTBURY
WILLOW MEADOWS / WILLOWBEND AREA

In [89]:
#save this file for load trouble with foursquare
#houston_venues.to_pickle(r'C:\Users\Joe\JoeJupytrNbks\houston_venues_pkl.pkl')

In [90]:
#Read in file in case of internet/foursquare trouble
#houston_venues = pd.read_pickle(r'C:\Users\Joe\JoeJupytrNbks\houston_venues_pkl.pkl')

#### View the size of the resulting dataframe and a short data sample

In [91]:
print(houston_venues.shape)
houston_venues.head()

(5009, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  FOURTH WARD              29.757116              -95.380766   
1  FOURTH WARD              29.757116              -95.380766   
2  FOURTH WARD              29.757116              -95.380766   
3  FOURTH WARD              29.757116              -95.380766   
4  FOURTH WARD              29.757116              -95.380766   

                             Venue  Venue Latitude  Venue Longitude  \
0             Eleanor Tinsley Park       29.761440       -95.379271   
1      Oporto Fooding House & Wine       29.753179       -95.380243   
2               Buffalo Bayou Walk       29.762177       -95.375844   
3  The Fish Restaurant & Sushi Bar       29.752249       -95.376820   
4                   Barnaby's Cafe       29.753470       -95.387019   

          Venue Category  
0                   Park  
1  Portuguese Restaurant  
2                  Trail  
3       Sushi Restaurant  
4    American Restaurant

Calculate how many venues were returned for each neighborhood

In [92]:
houston_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                         
ACRES HOME                                                       8   
ADDICKS PARK TEN                                                 8   
AFTON OAKS / RIVER OAKS AREA                                   100   
ALIEF                                                           66   
ASTRODOME AREA                                                  73   
BRAEBURN                                                        75   
BRAESWOOD                                                      100   
BRAYS OAKS                                                      58   
BRIAR FOREST                                                   100   
CARVERDALE                                                      21   
CENTRAL NORTHWEST                                               79   
CENTRAL SOUTHWEST                                               10   
CLEAR LAKE                                                      49   
CLINTON PARK TRI-COMMUNITY                                       4   
DENVER HARBOR / PORT HOUSTON                                    30   
DOWNTOWN                                                       100   
EAST HOUSTON                                                    18   
EAST LITTLE YORK / HOMESTEAD                                    10   
EASTEX - JENSEN AREA                                            19   
EDGEBROOK AREA                                                  57   
EL DORADO / OATES PRAIRIE                                        9   
ELDRIDGE / WEST OAKS                                            13   
FAIRBANKS / NORTHWEST CROSSING                                  78   
FONDREN GARDENS                                                 37   
FORT BEND HOUSTON                                               24   
FOURTH WARD                                                    100   
GOLFCREST / BELLFORT / REVEILLE                                 53   
GREATER EASTWOOD                                                86   
GREATER FIFTH WARD                                              27   
GREATER GREENSPOINT                                             78   
GREATER HEIGHTS                                                100   
GREATER HOBBY AREA                                              27   
GREATER INWOOD                                                  39   
GREATER OST / SOUTH UNION                                       42   
GREATER THIRD WARD                                              84   
GREATER UPTOWN                                                 100   
GREENWAY / UPPER KIRBY AREA                                    100   
GULFGATE RIVERVIEW / PINE VALLEY                                53   
GULFTON                                                        100   
HARRISBURG / MANCHESTER                                         13   
HIDDEN VALLEY                                                   33   
HUNTERWOOD                                                      10   
IAH / AIRPORT AREA                                              62   
INDEPENDENCE HEIGHTS                                            82   
KASHMERE GARDENS                                                24   
KINGWOOD AREA                                                   60   
LAKE HOUSTON                                                    24   
LANGWOOD                                                        56   
LAWNDALE / WAYSIDE                                              71   
LAZYBROOK / TIMBERGROVE                                         63   
MACGREGOR                                                       84   
MAGNOLIA PARK                                                   41   
MEADOWBROOK / ALLENDALE                                         19   
MEDICAL CENTER AREA                                            100   
MEMORIAL                                                        62   
MEYERLAND AREA                                         

#### View the number of unique categories from all the returned venues

In [93]:
print('There are {} uniques categories.'.format(len(houston_venues['Venue Category'].unique())))

There are 332 uniques categories.


<a id='item3'></a>

### 2C - Analyze General Categories for each Neighborhood

In [94]:
# one hot encoding
houston_onehot = pd.get_dummies(houston_venues[['Venue Category']], prefix="", prefix_sep="")

houston_onehot['Neighborhood'] = houston_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [houston_onehot.columns[-1]] + list(houston_onehot.columns[:-1])
houston_onehot = houston_onehot[fixed_columns]

houston_onehot.head(6)

Zoo Exhibit  Accessories Store  Adult Boutique  Advertising Agency  \
0            0                  0               0                   0   
1            0                  0               0                   0   
2            0                  0               0                   0   
3            0                  0               0                   0   
4            0                  0               0                   0   
5            0                  0               0                   0   

   Afghan Restaurant  African Restaurant  Airport  Airport Food Court  \
0                  0                   0        0                   0   
1                  0                   0        0                   0   
2                  0                   0        0                   0   
3                  0                   0        0                   0   
4                  0                   0        0                   0   
5                  0                   0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    1   
5               0                0                 0                    0   

   Antique Shop  Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0             0       0                       0            0           0   
1             0       0                       0            0           0   
2             0       0                       0            0           0   
3             0       0                       0            0           0   
4             0       0                       0            0           0   
5             0       0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   
5                    0                 0                   0                0   

   Auto Garage  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0            0                0          0           0       0     0    0   
1            0                0          0           0       0     0    0   
2            0                0          0           0       0     0    0   
3            0                0          0           0       0     0    0   
4            0                0          0           0       0     0    0   
5            0                0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   
5               0                 0                 0                   0   

   Bay  Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Shop  \
0    0         0            0           0              0          0   
1    0         0            0           0              0          0   
2    0         0            0           0    

And let's examine the new dataframe size.

In [95]:
houston_onehot.shape


(5009, 332)

#### Group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [96]:
houston_grouped = houston_onehot.groupby('Neighborhood').mean().reset_index()
houston_grouped

Neighborhood  Zoo Exhibit  \
0                                    ACRES HOME         0.00   
1                              ADDICKS PARK TEN         0.00   
2                  AFTON OAKS / RIVER OAKS AREA         0.00   
3                                         ALIEF         0.00   
4                                ASTRODOME AREA         0.00   
5                                      BRAEBURN         0.00   
6                                     BRAESWOOD         0.00   
7                                    BRAYS OAKS         0.00   
8                                  BRIAR FOREST         0.00   
9                                    CARVERDALE         0.00   
10                            CENTRAL NORTHWEST         0.00   
11                            CENTRAL SOUTHWEST         0.00   
12                                   CLEAR LAKE         0.00   
13                   CLINTON PARK TRI-COMMUNITY         0.00   
14                 DENVER HARBOR / PORT HOUSTON         0.00   
15                                     DOWNTOWN         0.00   
16                                 EAST HOUSTON         0.00   
17                 EAST LITTLE YORK / HOMESTEAD         0.00   
18                         EASTEX - JENSEN AREA         0.00   
19                               EDGEBROOK AREA         0.00   
20                    EL DORADO / OATES PRAIRIE         0.00   
21                         ELDRIDGE / WEST OAKS         0.00   
22               FAIRBANKS / NORTHWEST CROSSING         0.00   
23                              FONDREN GARDENS         0.00   
24                            FORT BEND HOUSTON         0.00   
25                                  FOURTH WARD         0.00   
26              GOLFCREST / BELLFORT / REVEILLE         0.00   
27                             GREATER EASTWOOD         0.00   
28                           GREATER FIFTH WARD         0.00   
29                          GREATER GREENSPOINT         0.00   
30                              GREATER HEIGHTS         0.00   
31                           GREATER HOBBY AREA         0.00   
32                               GREATER INWOOD         0.00   
33                    GREATER OST / SOUTH UNION         0.00   
34                           GREATER THIRD WARD         0.00   
35                               GREATER UPTOWN         0.00   
36                  GREENWAY / UPPER KIRBY AREA         0.00   
37             GULFGATE RIVERVIEW / PINE VALLEY         0.00   
38                                      GULFTON         0.00   
39                      HARRISBURG / MANCHESTER         0.00   
40                                HIDDEN VALLEY         0.00   
41                                   HUNTERWOOD         0.00   
42                           IAH / AIRPORT AREA         0.00   
43                         INDEPENDENCE HEIGHTS         0.00   
44                             KASHMERE GARDENS         0.00   
45                                KINGWOOD AREA         0.00   
46                                 LAKE HOUSTON         0.00   
47                                     LANGWOOD         0.00   
48                           LAWNDALE / WAYSIDE         0.00   
49                      LAZYBROOK / TIMBERGROVE         0.00   
50                                    MACGREGOR         0.00   
51                                MAGNOLIA PARK         0.00   
52                      MEADOWBROOK / ALLENDALE         0.00   
53                          MEDICAL CENTER AREA         0.13   
54                                     MEMORIAL         0.00   
55                               MEYERLAND AREA         0.00   
56                                     MID WEST         0.00   
57                                      MIDTOWN         0.00   
58                                     MINNETEX         0.00   
59                                  MUSEUM PARK         0.12   
60                               NEAR NORTHSIDE         0.00   
61                          NEARTOWN - MONTROSE         0.00   
62 

#### Confirm the new size

In [97]:
houston_grouped.shape

(88, 332)

#### Let's print each neighborhood along with the top 5 most common venues

In [98]:
num_top_venues = 5

for hood in houston_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = houston_grouped[houston_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----ACRES HOME----
                        venue  freq
0  Construction & Landscaping  0.12
1                        Food  0.12
2              Baseball Field  0.12
3               Grocery Store  0.12
4          Seafood Restaurant  0.12


----ADDICKS PARK TEN----
                 venue  freq
0                 Park  0.38
1  Government Building  0.12
2       Baseball Field  0.12
3              Dog Run  0.12
4         Tennis Court  0.12


----AFTON OAKS / RIVER OAKS AREA----
                venue  freq
0  Mexican Restaurant  0.04
1    Sushi Restaurant  0.04
2  Salon / Barbershop  0.04
3  Seafood Restaurant  0.03
4   French Restaurant  0.03


----ALIEF----
                   venue  freq
0  Vietnamese Restaurant  0.11
1   Fast Food Restaurant  0.09
2         Discount Store  0.06
3            Pizza Place  0.06
4          Grocery Store  0.05


----ASTRODOME AREA----
                 venue  freq
0           Food Truck  0.04
1       Sandwich Place  0.04
2           Restaurant  0.04
3        Groce

#### Convert into a *pandas* dataframe

Define a function to sort the venues in descending order.

In [99]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Create the new dataframe and display the top 10 venues for each neighborhood.

In [100]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = houston_grouped['Neighborhood']

for ind in np.arange(houston_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(houston_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood  1st Most Common Venue 2nd Most Common Venue  \
0                    ACRES HOME                   Food    Seafood Restaurant   
1              ADDICKS PARK TEN                   Park               Dog Run   
2  AFTON OAKS / RIVER OAKS AREA     Salon / Barbershop    Mexican Restaurant   
3                         ALIEF  Vietnamese Restaurant  Fast Food Restaurant   
4                ASTRODOME AREA         Sandwich Place            Food Truck   

        3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0  Construction & Landscaping           Baseball Field                  Park   
1                Tennis Court    Outdoors & Recreation   Government Building   
2            Sushi Restaurant  New American Restaurant     French Restaurant   
3                 Pizza Place           Discount Store           Gas Station   
4                  Restaurant     Gym / Fitness Center   American Restaurant   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
0         Grocery Store               Rental Service        Discount Store   
1        Baseball Field  Eastern European Restaurant            Donut Shop   
2    Seafood Restaurant                          Gym          Burger Joint   
3           Video Store                Grocery Store       Bubble Tea Shop   
4    Italian Restaurant          Filipino Restaurant                   Bar   

  9th Most Common Venue     10th Most Common Venue  
0        Duty-free Shop                    Dog Run  
1           Dry Cleaner        Dumpling Restaurant  
2                  Café         Italian Restaurant  
3        Sandwich Place  Cajun / Creole Restaurant  
4             BBQ Joint                Gas Station

In [101]:
neighborhoods_venues_sorted.shape

(88, 11)

### 2D - Cluster Analysis using general categories for Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [102]:
# set number of clusters
kclusters = 6

grouped_clustering = houston_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 4, 0, 5, 0, 5, 0, 5, 0, 5])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [103]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

neighborhood_merged =  neighborhood_list

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
neighborhood_merged = neighborhood_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

neighborhood_merged.head() # check the last columns!

OBJECTID  POLYID                Neighborhood     Shapearea        LAT  \
0         1      60                 FOURTH WARD  1.296982e+07  29.757116   
1         2      63                 SECOND WARD  8.040472e+07  29.750962   
2         3      61                    DOWNTOWN  7.550023e+07  29.756689   
3         4      59  CLINTON PARK TRI-COMMUNITY  7.655352e+07  29.748397   
4         5      21              GREATER UPTOWN  2.297921e+08  29.756552   

        LONG  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0 -95.380766               0           Coffee Shop           Pizza Place   
1 -95.327939               3    Mexican Restaurant        Discount Store   
2 -95.359096               0                 Hotel            Taco Place   
3 -95.262714               4    Athletics & Sports                  Park   
4 -95.475614               0   American Restaurant           Yoga Studio   

  3rd Most Common Venue 4th Most Common Venue  5th Most Common Venue  \
0                   Bar                  Park                Theater   
1  Fast Food Restaurant                   Bar            Gas Station   
2    Mexican Restaurant                   Bar  Vietnamese Restaurant   
3           Gas Station          Intersection                    Zoo   
4        Cosmetics Shop     French Restaurant     Mexican Restaurant   

  6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
0   American Restaurant        Sandwich Place               Food Truck   
1           Snack Place           Art Gallery                 Dive Bar   
2      Baseball Stadium            Steakhouse              Pizza Place   
3     Electronics Store            Donut Shop              Dry Cleaner   
4                 Hotel              Pharmacy  New American Restaurant   

   9th Most Common Venue 10th Most Common Venue  
0  Vietnamese Restaurant            Beer Garden  
1                   Park            Music Venue  
2            Coffee Shop                   Park  
3    Dumpling Restaurant         Duty-free Shop  
4             Food Truck            Coffee Shop

Visualize the resulting clusters on a map

In [104]:
# create map
#map_clusters = folium.Map(location=[LAT, LONG], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(neighborhood_merged['LAT'], neighborhood_merged['LONG'], neighborhood_merged['Neighborhood'], neighborhood_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(Hmap)
       
Hmap

### 2E - Examine general venue category Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 0

In [105]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 0, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels  \
0                                   FOURTH WARD               0   
2                                      DOWNTOWN               0   
4                                GREATER UPTOWN               0   
8                          ELDRIDGE / WEST OAKS               0   
9   WASHINGTON AVENUE COALITION / MEMORIAL PARK               0   
14                      LAZYBROOK / TIMBERGROVE               0   
15                              GREATER HEIGHTS               0   
36                                  WILLOWBROOK               0   
38                           IAH / AIRPORT AREA               0   
40                                 LAKE HOUSTON               0   
41               FAIRBANKS / NORTHWEST CROSSING               0   
60                               ASTRODOME AREA               0   
64                          MEDICAL CENTER AREA               0   
65                                      GULFTON               0   
69                             UNIVERSITY PLACE               0   
70                                    WESTCHASE               0   
71                                  MUSEUM PARK               0   
73                  GREENWAY / UPPER KIRBY AREA               0   
74                           GREATER THIRD WARD               0   
75                                     MID WEST               0   
76                             GREATER EASTWOOD               0   
77                                      MIDTOWN               0   
78                                    BRAESWOOD               0   
79                               MEYERLAND AREA               0   
82                 AFTON OAKS / RIVER OAKS AREA               0   
83                                 BRIAR FOREST               0   
84                          NEARTOWN - MONTROSE               0   
85                                     MEMORIAL               0   

        1st Most Common Venue 2nd Most Common Venue  3rd Most Common Venue  \
0                 Coffee Shop           Pizza Place                    Bar   
2                       Hotel            Taco Place     Mexican Restaurant   
4         American Restaurant           Yoga Studio         Cosmetics Shop   
8                         Bar               Dog Run                   Food   
9                         Bar    Mexican Restaurant                  Trail   
14                Gas Station    Mexican Restaurant                   Park   
15         Mexican Restaurant   American Restaurant            Coffee Shop   
36     Furniture / Home Store          Burger Joint            Coffee Shop   
38        Rental Car Location           Coffee Shop         Airport Lounge   
40         Mexican Restaurant  Fast Food Restaurant             Donut Shop   
41         Mexican Restaurant  Fast Food Restaurant                  Hotel   
60             Sandwich Place            Food Truck             Restaurant   
64                Zoo Exhibit            Food Truck                  Hotel   
65          Indian Restaurant    Mexican Restaurant            Coffee Shop   
69                Coffee Shop           Zoo Exhibit    American Restaurant   
70                      Hotel        Sandwich Place          Grocery Store   
71                Zoo Exhibit           Coffee Shop                    Bar   
73         Mexican Restaurant    Italian Restaurant            Coffee Shop   
74                Coffee Shop           Pizza Place                    Bar   
75  Middle Eastern Restaurant     Indian Restaurant     Mexican Restaurant   
76                Coffee Shop                   Bar            Pizza Place   
77                Coffee Shop                   Bar  Vietnamese Restaurant   
78         Mexican Restaurant           Coffee Shop             Donut Shop   
79                Pizza Place           Coffee Shop       Department Store   
82         Salon / Barbershop    Mexican Restaurant       Sushi Restaurant   
83             Sandwich Place         Grocery Store            

#### Cluster 1

In [106]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 1, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
6   GREATER HOBBY AREA               1      Airport Terminal   
17            MINNETEX               1          Home Service   
50   CENTRAL SOUTHWEST               1   Fried Chicken Joint   
59          SOUTH PARK               1           Gas Station   

         2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
6                Grocery Store    Mexican Restaurant           Gas Station   
17  Construction & Landscaping        Shipping Store        Discount Store   
50                        Park        Shop & Service           Gas Station   
59                  Donut Shop          Burger Joint      Greek Restaurant   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
6                      Airport        Ice Cream Shop        Discount Store   
17                        Lake           Gas Station           Auto Garage   
50  Construction & Landscaping     Convenience Store           Bus Station   
59                Intersection        Sandwich Place           Coffee Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
6         Sandwich Place        Scenic Lookout             Food Truck  
17        Farmers Market            Eye Doctor            Event Space  
50      Basketball Court          Intersection                    Zoo  
59    Chinese Restaurant        Cosmetics Shop               Pharmacy

#### Cluster 2

In [107]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 2, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
28     TRINITY / HOUSTON GARDENS               2        Discount Store   
30          EASTEX - JENSEN AREA               2        Discount Store   
32                    ACRES HOME               2                  Food   
35  EAST LITTLE YORK / HOMESTEAD               2        Discount Store   
45             FORT BEND HOUSTON               2        Discount Store   
48  SOUTH ACRES / CRESTMONT PARK               2         Grocery Store   
55                      WESTBURY               2           Pizza Place   
63       MEADOWBROOK / ALLENDALE               2          Liquor Store   

   2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
28             BBQ Joint         American Restaurant                Bakery   
30  Fast Food Restaurant                 Pizza Place           Gas Station   
32    Seafood Restaurant  Construction & Landscaping        Baseball Field   
35          Home Service                  Food Truck     Convenience Store   
45         Grocery Store          Seafood Restaurant  Fast Food Restaurant   
48           Gas Station              Discount Store             Pet Store   
55        Discount Store              Baseball Field            Food Truck   
63        Discount Store                 Golf Course        Baseball Field   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
28  Construction & Landscaping      Department Store           Gas Station   
30              Sandwich Place                  Food               Brewery   
32                        Park         Grocery Store        Rental Service   
35                     Brewery   Fried Chicken Joint           Gas Station   
45                 Pizza Place     Convenience Store           Gas Station   
48               Go Kart Track          Cocktail Bar     Convenience Store   
55               Grocery Store                   Gym          Tennis Court   
63                      Casino         Grocery Store           Gas Station   

     8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
28           Event Service    Dumpling Restaurant         Duty-free Shop  
30     Fried Chicken Joint                   Bank      Other Repair Shop  
32          Discount Store         Duty-free Shop                Dog Run  
35                    Park    Empanada Restaurant    Dumpling Restaurant  
45          Sandwich Place  Check Cashing Service             Food Truck  
48                Pharmacy      Mobile Phone Shop     Seafood Restaurant  
55                     Bar             Donut Shop           Dance Studio  
63  Thrift / Vintage Store            Video Store             Food Truck

#### Cluster 3

In [108]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 3, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
1                    SECOND WARD               3    Mexican Restaurant   
11  DENVER HARBOR / PORT HOUSTON               3    Mexican Restaurant   
12            PLEASANTVILLE AREA               3           Gas Station   
18                NEAR NORTHSIDE               3    Mexican Restaurant   
20           SPRING BRANCH NORTH               3    Mexican Restaurant   
21     EL DORADO / OATES PRAIRIE               3    Mexican Restaurant   
22         SPRING BRANCH CENTRAL               3    Mexican Restaurant   
24                     SETTEGAST               3   American Restaurant   
62                    PARK PLACE               3           Gas Station   
81                 MAGNOLIA PARK               3    Mexican Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1         Discount Store  Fast Food Restaurant                   Bar   
11           Gas Station  Fast Food Restaurant         Boat or Ferry   
12  Fast Food Restaurant    Mexican Restaurant        Sandwich Place   
18        Discount Store                  Park   Fried Chicken Joint   
20           Pizza Place         Grocery Store   Fried Chicken Joint   
21           Gas Station   Rental Car Location                Office   
22        Sandwich Place  Gym / Fitness Center              Pharmacy   
24          Burger Joint                  Food     Other Repair Shop   
62        Discount Store        Baseball Field           Pizza Place   
81  Fast Food Restaurant    Seafood Restaurant   Fried Chicken Joint   

    5th Most Common Venue       6th Most Common Venue 7th Most Common Venue  \
1             Gas Station                 Snack Place           Art Gallery   
11    Fried Chicken Joint         American Restaurant        Discount Store   
12                Brewery                      Office       Automotive Shop   
18   Fast Food Restaurant              Sandwich Place          Concert Hall   
20         Discount Store       Vietnamese Restaurant                  Café   
21         Sandwich Place              Ice Cream Shop     Electronics Store   
22  Vietnamese Restaurant                Burger Joint           Video Store   
24     Mexican Restaurant  Construction & Landscaping     Convenience Store   
62     Mexican Restaurant                 Golf Course    Seafood Restaurant   
81            Snack Place                 Pizza Place     Convenience Store   

        8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1                    Dive Bar                  Park            Music Venue  
11                       Food          Burger Joint             Skate Park  
12  Latin American Restaurant            Taco Place           Intersection  
18                 Food Truck           Gas Station            Video Store  
20       Gym / Fitness Center                  Park           Burger Joint  
21                 Donut Shop           Dry Cleaner    Dumpling Restaurant  
22     Thrift / Vintage Store        Discount Store      Korean Restaurant  
24                Gas Station        Discount Store         Sandwich Place  
62             Sandwich Place           Supermarket    Rental Car Location  
81              Grocery Store           Gas Station         Baseball Field

#### Cluster 4

In [109]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 4, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
3   CLINTON PARK TRI-COMMUNITY               4    Athletics & Sports   
68     HARRISBURG / MANCHESTER               4                  Park   
87            ADDICKS PARK TEN               4                  Park   

   2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
3                   Park           Gas Station           Intersection   
68         Boat or Ferry       Harbor / Marina   Fast Food Restaurant   
87               Dog Run          Tennis Court  Outdoors & Recreation   

   5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
3                    Zoo     Electronics Store                   Donut Shop   
68         Moving Target           Supermarket                  Gas Station   
87   Government Building        Baseball Field  Eastern European Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3            Dry Cleaner   Dumpling Restaurant         Duty-free Shop  
68        Discount Store    Mexican Restaurant            Pizza Place  
87            Donut Shop           Dry Cleaner    Dumpling Restaurant

##### Cluster 5

In [110]:
neighborhood_merged.loc[neighborhood_merged['Cluster Labels'] == 5, neighborhood_merged.columns[[2] + list(range(6, neighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels  1st Most Common Venue  \
5                     GREATER INWOOD               5   Fast Food Restaurant   
7    GOLFCREST / BELLFORT / REVEILLE               5   Fast Food Restaurant   
10                GREATER FIFTH WARD               5           Intersection   
13                        NORTHSHORE               5     Mexican Restaurant   
16                  KASHMERE GARDENS               5    Fried Chicken Joint   
19                SPRING BRANCH EAST               5   Fast Food Restaurant   
23                        HUNTERWOOD               5    Fried Chicken Joint   
25                          LANGWOOD               5                  Hotel   
26              INDEPENDENCE HEIGHTS               5      Mobile Phone Shop   
27                 CENTRAL NORTHWEST               5     Mexican Restaurant   
29                        CARVERDALE               5                  Hotel   
31                      EAST HOUSTON               5   Fast Food Restaurant   
33               NORTHSIDE/NORTHLINE               5   Fast Food Restaurant   
34                     HIDDEN VALLEY               5   Fast Food Restaurant   
37               GREATER GREENSPOINT               5   Fast Food Restaurant   
39                     KINGWOOD AREA               5            Pizza Place   
42                        WESTBRANCH               5                   Café   
43                        SHARPSTOWN               5               Pharmacy   
44                          WESTWOOD               5     Mexican Restaurant   
46                   FONDREN GARDENS               5   Fast Food Restaurant   
47            SOUTH BELT / ELLINGTON               5  Vietnamese Restaurant   
49                        BRAYS OAKS               5   Fast Food Restaurant   
51                         SUNNYSIDE               5    Fried Chicken Joint   
52                             ALIEF               5  Vietnamese Restaurant   
53                        PECAN PARK               5            Pizza Place   
54                        CLEAR LAKE               5            Pizza Place   
56  WILLOW MEADOWS / WILLOWBEND AREA               5            Gas Station   
57                          BRAEBURN               5         Sandwich Place   
58                        SOUTH MAIN               5   Fast Food Restaurant   
61         GREATER OST / SOUTH UNION               5   Fast Food Restaurant   
66                         MACGREGOR               5   Fast Food Restaurant   
67  GULFGATE RIVERVIEW / PINE VALLEY               5   Fast Food Restaurant   
72                LAWNDALE / WAYSIDE               5     Mexican Restaurant   
80                    EDGEBROOK AREA               5     Mexican Restaurant   
86                SPRING BRANCH WEST               5   Fast Food Restaurant   

   2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
5            Pizza Place   Fried Chicken Joint         Discount Store   
7            Pizza Place    Mexican Restaurant         Discount Store   
10              Pharmacy                  Park   Fast Food Restaurant   
13  Fast Food Restaurant        Discount Store         Sandwich Place   
16  Fast Food Restaurant        Discount Store               Bus Stop   
19                  Bank    Mexican Restaurant  Vietnamese Restaurant   
23  Gym / Fitness Center                  Food             Donut Shop   
25  Fast Food Restaurant           Gas Station         Sandwich Place   
26        Discount Store    Mexican Restaurant    Fried Chicken Joint   
27                  Park           Gas Station                  Trail   
29           Gas Station             BBQ Joint         Sandwich Place   
31         Grocery Store        Discount Store    Fried Chicken Joint   
33   Fried Chicken Joint        Sandwich Place     Mexican Restaurant   
34           Gas Station         Grocery Store               Pharmacy   
37    Mexican Restaurant           Pizza Place                  Hotel   
39  Fast Fo

In [212]:
neighborhood_merged.groupby('Cluster Labels').count()
#ffvenues.groupby('Neighborhood').count()

OBJECTID  POLYID  Neighborhood  Shapearea  LAT  LONG  \
Cluster Labels                                                         
0                     28      28            28         28   28    28   
1                      4       4             4          4    4     4   
2                      8       8             8          8    8     8   
3                     10      10            10         10   10    10   
4                      3       3             3          3    3     3   
5                     35      35            35         35   35    35   

                1st Most Common Venue  2nd Most Common Venue  \
Cluster Labels                                                 
0                                  28                     28   
1                                   4                      4   
2                                   8                      8   
3                                  10                     10   
4                                   3                      3   
5                                  35                     35   

                3rd Most Common Venue  4th Most Common Venue  \
Cluster Labels                                                 
0                                  28                     28   
1                                   4                      4   
2                                   8                      8   
3                                  10                     10   
4                                   3                      3   
5                                  35                     35   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                  28                     28   
1                                   4                      4   
2                                   8                      8   
3                                  10                     10   
4                                   3                      3   
5                                  35                     35   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                  28                     28   
1                                   4                      4   
2                                   8                      8   
3                                  10                     10   
4                                   3                      3   
5                                  35                     35   

                9th Most Common Venue  10th Most Common Venue  
Cluster Labels                                                 
0                                  28                      28  
1                                   4                       4  
2                                   8                       8  
3                                  10                      10  
4                                   3                       3  
5                                  35                      35

In [111]:
#end Part 1 General Venue Category Analysis

### **PART 3 Fast Food Specific Neighborhood Comparison**

### 3A - Define Foursquare Credentials and Version 

re-use Part2 section 2A

### 3B - Get Fast Food Venues only for Neighborhoods in Houston

Re-use Part2 section 2B

Start with results for all venues from section 2B  dataframe : houston_venues and filter to fast food venues

#### Data Prep - clean popular fast food restaurants names to be exactly the same

In [112]:
houston_venues = houston_venues.replace(["McDonald's"],'McDonalds')
houston_venues = houston_venues.replace(["Wendy's"],'Wendys')
houston_venues = houston_venues.replace(["Church's Chicken"],'Churchs Chicken')
houston_venues = houston_venues.replace(['What A Burger'],'Whataburger')
houston_venues = houston_venues.replace(['Sonic Drive-In'],'SONIC Drive In')
houston_venues = houston_venues.replace(['Subway'],'SUBWAY')

In [113]:
houston_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  FOURTH WARD              29.757116              -95.380766   
1  FOURTH WARD              29.757116              -95.380766   
2  FOURTH WARD              29.757116              -95.380766   
3  FOURTH WARD              29.757116              -95.380766   
4  FOURTH WARD              29.757116              -95.380766   

                             Venue  Venue Latitude  Venue Longitude  \
0             Eleanor Tinsley Park       29.761440       -95.379271   
1      Oporto Fooding House & Wine       29.753179       -95.380243   
2               Buffalo Bayou Walk       29.762177       -95.375844   
3  The Fish Restaurant & Sushi Bar       29.752249       -95.376820   
4                   Barnaby's Cafe       29.753470       -95.387019   

          Venue Category  
0                   Park  
1  Portuguese Restaurant  
2                  Trail  
3       Sushi Restaurant  
4    American Restaurant

Note: Getting fast food restaurants as a single category is not a trivial task and we built our own fast food category by filtering for specific fast food franchise names. In our WhataBurger example, the raw download data had the venue categorized both as a "burger joint" and as "fast food restaurant". This is a common occurrence in the FourSquare database and appears to be challenging to always import the "fast food" category into the pandas databases for analysis. It is also worth noting that some peculiarities exist in querying venue data within FourSqare. Fast Food Query results frequently pull more than "fast food" venues. 


In [114]:
# Basic Fast Food Franchise filter
ffvenues = houston_venues[(houston_venues.Venue == 'McDonalds') | (houston_venues.Venue == 'Burger King')|  
                         (houston_venues.Venue == 'SONIC Drive In') | (houston_venues.Venue == 'Wendys') | 
                         (houston_venues.Venue == 'KFC') | (houston_venues.Venue == 'Wendys') | 
                         (houston_venues.Venue == 'Taco Bell') | (houston_venues.Venue == 'Chick fil A') | 
                         (houston_venues.Venue == 'Churchs Chicken') | (houston_venues.Venue == 'Jack in the Box') | 
                         (houston_venues.Venue == 'Whataburger') | (houston_venues.Venue == 'SUBWAY')]
    
#ffvenues

In [115]:
print(ffvenues.shape)
ffvenues.head()

#ffvenues.columns

(350, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
113  SECOND WARD              29.750962              -95.327939   
129  SECOND WARD              29.750962              -95.327939   
135  SECOND WARD              29.750962              -95.327939   
138  SECOND WARD              29.750962              -95.327939   
145  SECOND WARD              29.750962              -95.327939   

               Venue  Venue Latitude  Venue Longitude        Venue Category  
113  Jack in the Box       29.755577       -95.335397  Fast Food Restaurant  
129           SUBWAY       29.754937       -95.336595        Sandwich Place  
135        McDonalds       29.751307       -95.322859  Fast Food Restaurant  
138  Churchs Chicken       29.744195       -95.327982   Fried Chicken Joint  
145  Jack in the Box       29.734520       -95.329300  Fast Food Restaurant

Let's check how many venues were returned for each neighborhood

In [116]:
ffvenues.groupby('Neighborhood').count()
#houston_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                              
AFTON OAKS / RIVER OAKS AREA                          1   
ALIEF                                                 9   
ASTRODOME AREA                                        4   
BRAEBURN                                              5   
BRAESWOOD                                             4   
BRAYS OAKS                                           12   
BRIAR FOREST                                          3   
CARVERDALE                                            1   
CENTRAL NORTHWEST                                     3   
CENTRAL SOUTHWEST                                     1   
CLEAR LAKE                                            2   
DENVER HARBOR / PORT HOUSTON                          5   
EAST HOUSTON                                          7   
EASTEX - JENSEN AREA                                  5   
EDGEBROOK AREA                                        7   
EL DORADO / OATES PRAIRIE                             1   
ELDRIDGE / WEST OAKS                                  1   
FAIRBANKS / NORTHWEST CROSSING                        7   
FONDREN GARDENS                                       5   
FORT BEND HOUSTON                                     3   
GOLFCREST / BELLFORT / REVEILLE                       9   
GREATER EASTWOOD                                      8   
GREATER FIFTH WARD                                    3   
GREATER GREENSPOINT                                  10   
GREATER HOBBY AREA                                    2   
GREATER INWOOD                                        6   
GREATER OST / SOUTH UNION                             9   
GREATER THIRD WARD                                    8   
GREENWAY / UPPER KIRBY AREA                           2   
GULFGATE RIVERVIEW / PINE VALLEY                      6   
GULFTON                                               3   
HIDDEN VALLEY                                         6   
HUNTERWOOD                                            4   
IAH / AIRPORT AREA                                    2   
INDEPENDENCE HEIGHTS                                  7   
KASHMERE GARDENS                                      6   
KINGWOOD AREA                                         5   
LAKE HOUSTON                                          2   
LANGWOOD                                              4   
LAWNDALE / WAYSIDE                                   10   
LAZYBROOK / TIMBERGROVE                               2   
MACGREGOR                                            12   
MAGNOLIA PARK                                         6   
MEADOWBROOK / ALLENDALE                               1   
MEDICAL CENTER AREA                                   4   
MEMORIAL                                              3   
MEYERLAND AREA                                        5   
MID WEST                                              1   
NEAR NORTHSIDE                                        9   
NORTHSHORE                                            9   
NORTHSIDE/NORTHLINE                                   8   
PARK PLACE                                            1   
PECAN PARK                                            5   
PLEASANTVILLE AREA                                    6   
SECOND WARD                                           5   
SETTEGAST                                             1   
SHARPSTOWN                                            6   
SOUTH BELT / ELLINGTON                                7   
SOUTH MAIN                                            9   
SOUTH PARK                                            2   
SPRING BRANCH CENTRAL                                 4   
SPRING BRANCH EAST                                    7   
SPRING BRANCH NORTH                                   4   
SPRING BRANCH WEST                                   10   
SUNNYSIDE                                             4   
TRINITY / HOUSTON GARDENS                             1   
WESTBRANCH            

In [117]:
#ffvenuesffvenuesffvenues.dtypes
#ffvenuesffvenues.columns
ffvenues.index

Int64Index([ 113,  129,  135,  138,  145,  372,  376,  380,  385,  386,
            ...
            4955, 4958, 4963, 4964, 4972, 4974, 4975, 4985, 4987, 4990],
           dtype='int64', length=350)

#### Let's find out how many unique venues can be curated from all the returned fast food venues

In [118]:
print('There are {} selected fast food venues.'.format(len(ffvenues['Venue'].unique())))

There are 10 selected fast food venues.


<a id='item3'></a>

### 3C - Analyze fast food venue specific restaurants for each Neighborhood

In [119]:
# one hot encoding
ffhouston_onehot = pd.get_dummies(ffvenues[['Venue']], prefix="", prefix_sep="")

ffhouston_onehot['Neighborhood'] = ffvenues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ffhouston_onehot.columns[-1]] + list(ffhouston_onehot.columns[:-1])
ffhouston_onehot = ffhouston_onehot[fixed_columns]

ffhouston_onehot.head(6)

Neighborhood  Burger King  Churchs Chicken  Jack in the Box  KFC  \
113     SECOND WARD            0                0                1    0   
129     SECOND WARD            0                0                0    0   
135     SECOND WARD            0                0                0    0   
138     SECOND WARD            0                1                0    0   
145     SECOND WARD            0                0                1    0   
372  GREATER INWOOD            0                0                0    0   

     McDonalds  SONIC Drive In  SUBWAY  Taco Bell  Wendys  Whataburger  
113          0               0       0          0       0            0  
129          0               0       1          0       0            0  
135          1               0       0          0       0            0  
138          0               0       0          0       0            0  
145          0               0       0          0       0            0  
372          0               0       1          0       0            0

examine the new fast food dataframe size.

In [120]:
ffhouston_onehot.shape

(350, 11)

#### Group rows by neighborhood and by taking the mean of the frequency of occurrence of each fast food chain

In [213]:
ffhouston_grouped = ffhouston_onehot.groupby('Neighborhood').mean().reset_index()
ffhouston_grouped.head()

Neighborhood  Burger King  Churchs Chicken  \
0  AFTON OAKS / RIVER OAKS AREA     0.000000         0.000000   
1                         ALIEF     0.111111         0.111111   
2                ASTRODOME AREA     0.000000         0.000000   
3                      BRAEBURN     0.000000         0.200000   
4                     BRAESWOOD     0.000000         0.000000   

   Jack in the Box  KFC  McDonalds  SONIC Drive In    SUBWAY  Taco Bell  \
0         0.000000  0.0   0.000000        0.000000  0.000000   0.000000   
1         0.111111  0.0   0.111111        0.111111  0.222222   0.222222   
2         0.000000  0.0   0.250000        0.000000  0.750000   0.000000   
3         0.000000  0.0   0.000000        0.000000  0.600000   0.000000   
4         0.000000  0.0   0.000000        0.250000  0.500000   0.000000   

   Wendys  Whataburger  
0     0.0         1.00  
1     0.0         0.00  
2     0.0         0.00  
3     0.0         0.20  
4     0.0         0.25

#### Confirm the new size

In [125]:
ffhouston_grouped.shape

(71, 11)

#### Print each neighborhood along with the top 5 most common venues

In [126]:
num_top_venues = 5

for hood in ffhouston_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ffhouston_grouped[ffhouston_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----AFTON OAKS / RIVER OAKS AREA----
             venue  freq
0      Whataburger   1.0
1      Burger King   0.0
2  Churchs Chicken   0.0
3  Jack in the Box   0.0
4              KFC   0.0


----ALIEF----
             venue  freq
0           SUBWAY  0.22
1        Taco Bell  0.22
2      Burger King  0.11
3  Churchs Chicken  0.11
4  Jack in the Box  0.11


----ASTRODOME AREA----
             venue  freq
0           SUBWAY  0.75
1        McDonalds  0.25
2      Burger King  0.00
3  Churchs Chicken  0.00
4  Jack in the Box  0.00


----BRAEBURN----
             venue  freq
0           SUBWAY   0.6
1  Churchs Chicken   0.2
2      Whataburger   0.2
3      Burger King   0.0
4  Jack in the Box   0.0


----BRAESWOOD----
             venue  freq
0           SUBWAY  0.50
1   SONIC Drive In  0.25
2      Whataburger  0.25
3      Burger King  0.00
4  Churchs Chicken  0.00


----BRAYS OAKS----
             venue  freq
0           SUBWAY  0.25
1      Burger King  0.17
2  Churchs Chicken  0.17
3  Jack in t

#### Let's put that into a *pandas* dataframe

Use a function to sort the venues in descending order.
return_most_common_venues function defined in Part 2 section 2C

Create the new dataframe and display the top 10 venues for each neighborhood.

In [197]:
num_top_ffvenues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_ffvenues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
ffneighborhoods_venues_sorted = pd.DataFrame(columns=columns)
ffneighborhoods_venues_sorted['Neighborhood'] = ffhouston_grouped['Neighborhood']

for ind in np.arange(ffhouston_grouped.shape[0]):
    ffneighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ffhouston_grouped.iloc[ind, :], num_top_ffvenues)

#neighborhoods_venues_sorted.head()
ffneighborhoods_venues_sorted

Neighborhood 1st Most Common Venue  \
0       AFTON OAKS / RIVER OAKS AREA           Whataburger   
1                              ALIEF             Taco Bell   
2                     ASTRODOME AREA                SUBWAY   
3                           BRAEBURN                SUBWAY   
4                          BRAESWOOD                SUBWAY   
5                         BRAYS OAKS                SUBWAY   
6                       BRIAR FOREST                SUBWAY   
7                         CARVERDALE                SUBWAY   
8                  CENTRAL NORTHWEST                SUBWAY   
9                  CENTRAL SOUTHWEST                   KFC   
10                        CLEAR LAKE                SUBWAY   
11      DENVER HARBOR / PORT HOUSTON           Whataburger   
12                      EAST HOUSTON        SONIC Drive In   
13              EASTEX - JENSEN AREA                SUBWAY   
14                    EDGEBROOK AREA                SUBWAY   
15         EL DORADO / OATES PRAIRIE                SUBWAY   
16              ELDRIDGE / WEST OAKS                SUBWAY   
17    FAIRBANKS / NORTHWEST CROSSING                SUBWAY   
18                   FONDREN GARDENS                SUBWAY   
19                 FORT BEND HOUSTON                SUBWAY   
20   GOLFCREST / BELLFORT / REVEILLE             McDonalds   
21                  GREATER EASTWOOD             Taco Bell   
22                GREATER FIFTH WARD             Taco Bell   
23               GREATER GREENSPOINT                SUBWAY   
24                GREATER HOBBY AREA                SUBWAY   
25                    GREATER INWOOD             Taco Bell   
26         GREATER OST / SOUTH UNION                SUBWAY   
27                GREATER THIRD WARD                SUBWAY   
28       GREENWAY / UPPER KIRBY AREA           Whataburger   
29  GULFGATE RIVERVIEW / PINE VALLEY       Jack in the Box   
30                           GULFTON           Whataburger   
31                     HIDDEN VALLEY                SUBWAY   
32                        HUNTERWOOD       Churchs Chicken   
33                IAH / AIRPORT AREA                SUBWAY   
34              INDEPENDENCE HEIGHTS                SUBWAY   
35                  KASHMERE GARDENS             Taco Bell   
36                     KINGWOOD AREA           Whataburger   
37                      LAKE HOUSTON             McDonalds   
38                          LANGWOOD                SUBWAY   
39                LAWNDALE / WAYSIDE                SUBWAY   
40           LAZYBROOK / TIMBERGROVE           Whataburger   
41                         MACGREGOR                SUBWAY   
42                     MAGNOLIA PARK       Jack in the Box   
43           MEADOWBROOK / ALLENDALE           Burger King   
44               MEDICAL CENTER AREA                SUBWAY   
45                          MEMORIAL           Whataburger   
46                    MEYERLAND AREA                SUBWAY   
47                          MID WEST                SUBWAY   
48                    NEAR NORTHSIDE                SUBWAY   
49                        NORTHSHORE                SUBWAY   
50               NORTHSIDE/NORTHLINE                SUBWAY   
51                        PARK PLACE                SUBWAY   
52                        PECAN PARK                SUBWAY   
53                PLEASANTVILLE AREA                SUBWAY   
54                       SECOND WARD       Jack in the Box   
55                         SETTEGAST                SUBWAY   
56                        SHARPSTOWN       Churchs Chicken   
57            SOUTH BELT / ELLINGTON                SUBWAY   
58                        SOUTH MAIN                SUBWAY   
59                        SOUTH PARK                SUBWAY   
60             SPRING BRANCH CENTRAL                SUBWAY   
61                SPRING BRANCH EAST                SUBWAY   
62               SPRING BRANCH NORTH           Whataburger   
63                SPRING BRANCH WEST                SUBW

In [198]:
ffneighborhoods_venues_sorted.shape

(71, 11)

### 3D - Cluster Analysis using fast food franchises only for Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [199]:
# set number of clusters
ffkclusters = 5

ffgrouped_clustering = ffhouston_grouped.drop('Neighborhood', 1)

# run k-means clustering
ffkmeans = KMeans(n_clusters=ffkclusters, random_state=0).fit(ffgrouped_clustering)

# check cluster labels generated for each row in the dataframe
ffkmeans.labels_[0:10] 
ffkmeans.labels_

array([3, 4, 2, 1, 1, 4, 2, 2, 2, 4, 2, 4, 4, 4, 1, 2, 2, 1, 1, 4, 4, 4,
       1, 4, 1, 4, 4, 1, 3, 4, 1, 4, 4, 1, 1, 4, 4, 0, 4, 4, 0, 4, 4, 0,
       1, 1, 1, 2, 4, 4, 4, 2, 1, 1, 4, 2, 4, 4, 4, 1, 1, 4, 4, 4, 4, 0,
       4, 1, 4, 1, 3])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [200]:
# add clustering labels
ffneighborhoods_venues_sorted.insert(0, 'Cluster Labels', ffkmeans.labels_)

ffneighborhood_merged =  neighborhood_list

# merge neighborhood list data with venue data to add latitude/longitude for each neighborhood
ffneighborhood_merged = ffneighborhood_merged.join(ffneighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [201]:
#neighborhood_merged = neighborhood_merged.replace(nan, 6)
ffcolorcluster = ffkclusters +1
ffneighborhood_merged['Cluster Labels'] = ffneighborhood_merged['Cluster Labels'].fillna(ffcolorcluster)

ffneighborhood_merged = ffneighborhood_merged.astype({"Cluster Labels": int})
ffneighborhood_merged.dropna(axis=0, how='any', thresh=None, inplace=True)

ffneighborhood_merged = ffneighborhood_merged.reset_index(drop=True)
ffneighborhood_merged.tail() # check the last columns!

OBJECTID  POLYID                  Neighborhood     Shapearea        LAT  \
66        85      82                 MAGNOLIA PARK  7.052141e+07  29.738742   
67        86      23  AFTON OAKS / RIVER OAKS AREA  1.006677e+08  29.747921   
68        87      18                  BRIAR FOREST  1.875152e+08  29.749193   
69         9      16                      MEMORIAL  2.753121e+08  29.773037   
70        22      10            SPRING BRANCH WEST  2.290214e+08  29.798845   

         LONG  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
66 -95.293816               4       Jack in the Box           Whataburger   
67 -95.435636               3           Whataburger                Wendys   
68 -95.574395               2                SUBWAY           Whataburger   
69 -95.584429               1           Whataburger                SUBWAY   
70 -95.560603               4                SUBWAY       Jack in the Box   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
66                SUBWAY       Churchs Chicken           Burger King   
67             Taco Bell                SUBWAY        SONIC Drive In   
68                Wendys             Taco Bell        SONIC Drive In   
69             McDonalds                Wendys             Taco Bell   
70             Taco Bell        SONIC Drive In             McDonalds   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
66                Wendys             Taco Bell        SONIC Drive In   
67             McDonalds                   KFC       Jack in the Box   
68             McDonalds                   KFC       Jack in the Box   
69        SONIC Drive In                   KFC       Jack in the Box   
70       Churchs Chicken           Burger King           Whataburger   

   9th Most Common Venue 10th Most Common Venue  
66             McDonalds                    KFC  
67       Churchs Chicken            Burger King  
68       Churchs Chicken            Burger King  
69       Churchs Chicken            Burger King  
70                Wendys                    KFC

#### Map the resulting fast food clusters

In [202]:
#Add one to kcluster for colored categary for missing value = 6
print(ffcolorcluster)

6


In [203]:
# create map. actually update Hmap
#Hmap = folium.Map(location=[LAT, LONG], zoom_start=11)

# set color scheme for the clusters
x = np.arange(ffcolorcluster)
ys = [i + x + (i*x)**2 for i in range(ffcolorcluster)]
ffcolors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
ffrainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ffneighborhood_merged['LAT'], ffneighborhood_merged['LONG'], ffneighborhood_merged['Neighborhood'], ffneighborhood_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=ffrainbow[cluster-1],
        fill=True,
        fill_color=ffrainbow[cluster-1],
        fill_opacity=0.7).add_to(Hmap)
       
Hmap

### 3E - Examine fast food venue category Clusters

Examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

#### Cluster 0

In [135]:
ffneighborhood_merged.loc[ffneighborhood_merged['Cluster Labels'] == 0, ffneighborhood_merged.columns[[2] + list(range(6, ffneighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
14    LAZYBROOK / TIMBERGROVE               0           Whataburger   
28  TRINITY / HOUSTON GARDENS               0             McDonalds   
40               LAKE HOUSTON               0             McDonalds   
63    MEADOWBROOK / ALLENDALE               0           Burger King   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
14           Burger King                Wendys             Taco Bell   
28           Whataburger                Wendys             Taco Bell   
40           Burger King           Whataburger                Wendys   
63           Whataburger                Wendys             Taco Bell   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
14                SUBWAY        SONIC Drive In             McDonalds   
28                SUBWAY        SONIC Drive In                   KFC   
40             Taco Bell                SUBWAY        SONIC Drive In   
63                SUBWAY        SONIC Drive In             McDonalds   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
14                   KFC       Jack in the Box        Churchs Chicken  
28       Jack in the Box       Churchs Chicken            Burger King  
40                   KFC       Jack in the Box        Churchs Chicken  
63                   KFC       Jack in the Box        Churchs Chicken

#### Cluster 1

In [136]:
ffneighborhood_merged.loc[ffneighborhood_merged['Cluster Labels'] == 1, ffneighborhood_merged.columns[[2] + list(range(6, ffneighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
6                 GREATER HOBBY AREA               1                SUBWAY   
10                GREATER FIFTH WARD               1             Taco Bell   
12                PLEASANTVILLE AREA               1                SUBWAY   
22             SPRING BRANCH CENTRAL               1                SUBWAY   
26              INDEPENDENCE HEIGHTS               1                SUBWAY   
38                IAH / AIRPORT AREA               1                SUBWAY   
41    FAIRBANKS / NORTHWEST CROSSING               1                SUBWAY   
46                   FONDREN GARDENS               1                SUBWAY   
53                        PECAN PARK               1                SUBWAY   
56  WILLOW MEADOWS / WILLOWBEND AREA               1           Whataburger   
57                          BRAEBURN               1                SUBWAY   
59                        SOUTH PARK               1                SUBWAY   
64               MEDICAL CENTER AREA               1                SUBWAY   
65                           GULFTON               1           Whataburger   
70                         WESTCHASE               1           Whataburger   
74                GREATER THIRD WARD               1                SUBWAY   
78                         BRAESWOOD               1                SUBWAY   
79                    MEYERLAND AREA               1                SUBWAY   
80                    EDGEBROOK AREA               1                SUBWAY   
85                          MEMORIAL               1           Whataburger   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
6        Jack in the Box           Whataburger                Wendys   
10                SUBWAY             McDonalds           Whataburger   
12           Whataburger             McDonalds       Jack in the Box   
22           Whataburger       Churchs Chicken                Wendys   
26           Whataburger             McDonalds                   KFC   
38             McDonalds           Whataburger                Wendys   
41           Whataburger             McDonalds       Jack in the Box   
46           Whataburger             Taco Bell       Jack in the Box   
53           Whataburger                   KFC       Churchs Chicken   
56                SUBWAY             McDonalds       Jack in the Box   
57           Whataburger       Churchs Chicken                Wendys   
59       Jack in the Box           Whataburger                Wendys   
64           Whataburger       Churchs Chicken                Wendys   
65                SUBWAY       Jack in the Box                Wendys   
70                SUBWAY                Wendys             Taco Bell   
74             Taco Bell             McDonalds       Churchs Chicken   
78           Whataburger        SONIC Drive In                Wendys   
79           Whataburger             McDonalds       Jack in the Box   
80           Whataburger             Taco Bell             McDonalds   
85                SUBWAY             McDonalds                Wendys   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
6              Taco Bell        SONIC Drive In             McDonalds   
10                Wendys        SONIC Drive In                   KFC   
12       Churchs Chicken                Wendys             Taco Bell   
22             Taco Bell        SONIC Drive In             McDonalds   
26       Churchs Chicken                Wendys             Taco Bell   
38             Taco Bell        SONIC Drive In                   KFC   
41           Burger King                Wendys             Taco Bell   
46                Wendys        SONIC Drive In             McDonalds   
53                Wendys             Taco Bell        SONIC Drive In   
56                Wendys             Taco Bell        SONIC Drive In   
57             Taco Bell        SONIC Drive In             McDonalds   
59      

#### Cluster 2

In [137]:
ffneighborhood_merged.loc[ffneighborhood_merged['Cluster Labels'] == 2, ffneighborhood_merged.columns[[2] + list(range(6, ffneighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
8        ELDRIDGE / WEST OAKS               2                SUBWAY   
21  EL DORADO / OATES PRAIRIE               2                SUBWAY   
24                  SETTEGAST               2                SUBWAY   
27          CENTRAL NORTHWEST               2                SUBWAY   
29                 CARVERDALE               2                SUBWAY   
54                 CLEAR LAKE               2                SUBWAY   
60             ASTRODOME AREA               2                SUBWAY   
62                 PARK PLACE               2                SUBWAY   
75                   MID WEST               2                SUBWAY   
83               BRIAR FOREST               2                SUBWAY   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8            Whataburger                Wendys             Taco Bell   
21           Whataburger                Wendys             Taco Bell   
24           Whataburger                Wendys             Taco Bell   
27       Churchs Chicken           Whataburger                Wendys   
29           Whataburger                Wendys             Taco Bell   
54           Whataburger                Wendys             Taco Bell   
60             McDonalds           Whataburger                Wendys   
62           Whataburger                Wendys             Taco Bell   
75           Whataburger                Wendys             Taco Bell   
83           Whataburger                Wendys             Taco Bell   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8         SONIC Drive In             McDonalds                   KFC   
21        SONIC Drive In             McDonalds                   KFC   
24        SONIC Drive In             McDonalds                   KFC   
27             Taco Bell        SONIC Drive In             McDonalds   
29        SONIC Drive In             McDonalds                   KFC   
54        SONIC Drive In             McDonalds                   KFC   
60             Taco Bell        SONIC Drive In                   KFC   
62        SONIC Drive In             McDonalds                   KFC   
75        SONIC Drive In             McDonalds                   KFC   
83        SONIC Drive In             McDonalds                   KFC   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
8        Jack in the Box       Churchs Chicken            Burger King  
21       Jack in the Box       Churchs Chicken            Burger King  
24       Jack in the Box       Churchs Chicken            Burger King  
27                   KFC       Jack in the Box            Burger King  
29       Jack in the Box       Churchs Chicken            Burger King  
54       Jack in the Box       Churchs Chicken            Burger King  
60       Jack in the Box       Churchs Chicken            Burger King  
62       Jack in the Box       Churchs Chicken            Burger King  
75       Jack in the Box       Churchs Chicken            Burger King  
83       Jack in the Box       Churchs Chicken            Burger King

#### Cluster 3

In [138]:
ffneighborhood_merged.loc[ffneighborhood_merged['Cluster Labels'] == 3, ffneighborhood_merged.columns[[2] + list(range(6, ffneighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
36                   WILLOWBROOK               3           Whataburger   
73   GREENWAY / UPPER KIRBY AREA               3           Whataburger   
82  AFTON OAKS / RIVER OAKS AREA               3           Whataburger   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
36                Wendys             Taco Bell                SUBWAY   
73                Wendys             Taco Bell                SUBWAY   
82                Wendys             Taco Bell                SUBWAY   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
36        SONIC Drive In             McDonalds                   KFC   
73        SONIC Drive In             McDonalds                   KFC   
82        SONIC Drive In             McDonalds                   KFC   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
36       Jack in the Box       Churchs Chicken            Burger King  
73       Jack in the Box       Churchs Chicken            Burger King  
82       Jack in the Box       Churchs Chicken            Burger King

#### Cluster 4

In [139]:
ffneighborhood_merged.loc[ffneighborhood_merged['Cluster Labels'] == 4, ffneighborhood_merged.columns[[2] + list(range(6, ffneighborhood_merged.shape[1]))]]

Neighborhood  Cluster Labels 1st Most Common Venue  \
1                        SECOND WARD               4       Jack in the Box   
5                     GREATER INWOOD               4             Taco Bell   
7    GOLFCREST / BELLFORT / REVEILLE               4             McDonalds   
11      DENVER HARBOR / PORT HOUSTON               4           Whataburger   
13                        NORTHSHORE               4                SUBWAY   
16                  KASHMERE GARDENS               4             Taco Bell   
18                    NEAR NORTHSIDE               4                SUBWAY   
19                SPRING BRANCH EAST               4                SUBWAY   
20               SPRING BRANCH NORTH               4           Whataburger   
23                        HUNTERWOOD               4       Churchs Chicken   
25                          LANGWOOD               4                SUBWAY   
30              EASTEX - JENSEN AREA               4                SUBWAY   
31                      EAST HOUSTON               4        SONIC Drive In   
33               NORTHSIDE/NORTHLINE               4                SUBWAY   
34                     HIDDEN VALLEY               4                SUBWAY   
37               GREATER GREENSPOINT               4                SUBWAY   
39                     KINGWOOD AREA               4           Whataburger   
42                        WESTBRANCH               4                SUBWAY   
43                        SHARPSTOWN               4       Churchs Chicken   
44                          WESTWOOD               4           Whataburger   
45                 FORT BEND HOUSTON               4                SUBWAY   
47            SOUTH BELT / ELLINGTON               4                SUBWAY   
49                        BRAYS OAKS               4                SUBWAY   
50                 CENTRAL SOUTHWEST               4                   KFC   
51                         SUNNYSIDE               4                SUBWAY   
52                             ALIEF               4             Taco Bell   
58                        SOUTH MAIN               4                SUBWAY   
61         GREATER OST / SOUTH UNION               4                SUBWAY   
66                         MACGREGOR               4                SUBWAY   
67  GULFGATE RIVERVIEW / PINE VALLEY               4       Jack in the Box   
72                LAWNDALE / WAYSIDE               4                SUBWAY   
76                  GREATER EASTWOOD               4             Taco Bell   
81                     MAGNOLIA PARK               4       Jack in the Box   
86                SPRING BRANCH WEST               4                SUBWAY   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1                 SUBWAY             McDonalds       Churchs Chicken   
5                 SUBWAY        SONIC Drive In             McDonalds   
7            Whataburger             Taco Bell                SUBWAY   
11                SUBWAY       Jack in the Box       Churchs Chicken   
13        SONIC Drive In             McDonalds                   KFC   
16                SUBWAY             McDonalds                   KFC   
18       Churchs Chicken             McDonalds           Whataburger   
19           Whataburger        SONIC Drive In             McDonalds   
20                SUBWAY                   KFC       Churchs Chicken   
23                SUBWAY        SONIC Drive In           Whataburger   
25             McDonalds       Churchs Chicken           Burger King   
30             McDonalds       Jack in the Box       Churchs Chicken   
31             Taco Bell                SUBWAY                   KFC   
33             McDonalds       Jack in the Box       Churchs Chicken   
34        SONIC Drive In             McDonalds       Jack in the Box   
37             McDonalds           Burger King           Whataburger   
39                SUBWAY        SONIC Drive In             McDonalds 

##### Cluster 5

In [211]:
ffneighborhood_merged.groupby('Cluster Labels').count()
#ffvenues.groupby('Neighborhood').count()

OBJECTID  POLYID  Neighborhood  Shapearea  LAT  LONG  \
Cluster Labels                                                         
0                      4       4             4          4    4     4   
1                     20      20            20         20   20    20   
2                     10      10            10         10   10    10   
3                      3       3             3          3    3     3   
4                     34      34            34         34   34    34   

                1st Most Common Venue  2nd Most Common Venue  \
Cluster Labels                                                 
0                                   4                      4   
1                                  20                     20   
2                                  10                     10   
3                                   3                      3   
4                                  34                     34   

                3rd Most Common Venue  4th Most Common Venue  \
Cluster Labels                                                 
0                                   4                      4   
1                                  20                     20   
2                                  10                     10   
3                                   3                      3   
4                                  34                     34   

                5th Most Common Venue  6th Most Common Venue  \
Cluster Labels                                                 
0                                   4                      4   
1                                  20                     20   
2                                  10                     10   
3                                   3                      3   
4                                  34                     34   

                7th Most Common Venue  8th Most Common Venue  \
Cluster Labels                                                 
0                                   4                      4   
1                                  20                     20   
2                                  10                     10   
3                                   3                      3   
4                                  34                     34   

                9th Most Common Venue  10th Most Common Venue  
Cluster Labels                                                 
0                                   4                       4  
1                                  20                      20  
2                                  10                      10  
3                                   3                       3  
4                                  34                      34

### **PART 4 Fast Food Restaurant Ratings for select Neighborhoods**

#### We limit the number of Neighborhoods to study because of FourSquare premium limitations.

####  The selcted Neighborhoods are: **Braeburn, Meyerland, Gulfton, and Sharpstown**

#### These neighborhoods were selected because they are in the same cluster or grouping for both the fast food venue analysis and the overall venue category analysis. They are also all on the west side of Houston

### 4A - Define Foursquare Credentials and Version 

re-use Part2 section 2A

### Set additional parametes needed for FourSquare URL requests

In [145]:
# parameters needed for foursquare url
LIMIT = 100 # limit of number of venues returned by Foursquare API
RADIUS = 2000 # define radius

### 4B - Get Fast Food Venues only for Neighborhoods in Houston

Bring original Neighborhood list from Part 1 and  filter for selected Neighborhoods

In [146]:
# TAKEN FROM POINT IN STEP 2 WHERE STEP THREE PICKS UP
#neighborhood_list.head()

In [147]:
# Filter for selected Neighborhoods for Ratings Analysis
Select_neighborhoods = neighborhood_list[(neighborhood_list.Neighborhood == "BRAEBURN") | 
                                     (neighborhood_list.Neighborhood == "MEYERLAND AREA") | 
                                     (neighborhood_list.Neighborhood == "GULFTON") | 
                                     (neighborhood_list.Neighborhood == "SHARPSTOWN")]
    
Select_neighborhoods

OBJECTID  POLYID    Neighborhood     Shapearea        LAT       LONG
43        46      26      SHARPSTOWN  2.380014e+08  29.703853 -95.524952
57        61      30        BRAEBURN  6.790817e+07  29.681566 -95.515667
65        69      27         GULFTON  7.895572e+07  29.713116 -95.481885
79        83      31  MEYERLAND AREA  1.145068e+08  29.679287 -95.477615

### 4C - Get Fast Food Venues only in selected Neighborhoods

#### Use modified getNearbyVenuen function to collect venue ID s for selected neighborhoods and individual fast food venues

In [148]:
def getNearbyFFVenues(names, latitudes, longitudes):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['id'], 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue ID',
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    # get specific fast food places
    nearby_venues = nearby_venues.replace(["McDonald's"],'McDonalds')
    nearby_venues = nearby_venues.replace(["Wendy's"],'Wendys')
    nearby_venues = nearby_venues.replace(["Church's Chicken"],'Churchs Chicken')
    nearby_venues = nearby_venues.replace(['What A Burger'],'Whataburger')
    nearby_venues = nearby_venues.replace(['Sonic Drive-In'],'SONIC Drive In')
    nearby_venues = nearby_venues.replace(['Subway'],'SUBWAY')
    
    #make names consistant
    # Basic Fast Food Franchise filter
    nearby_venues = nearby_venues[(nearby_venues.Venue == 'McDonalds') | (nearby_venues.Venue == 'Burger King')|  
                         (nearby_venues.Venue == 'SONIC Drive In') | (nearby_venues.Venue == 'Wendys') | 
                         (nearby_venues.Venue == 'KFC') | (nearby_venues.Venue == 'Wendys') | 
                         (nearby_venues.Venue == 'Taco Bell') | (nearby_venues.Venue == 'Chick fil A') | 
                         (nearby_venues.Venue == 'Churchs Chicken') | (nearby_venues.Venue == 'Jack in the Box') | 
                         (nearby_venues.Venue == 'Whataburger') | (nearby_venues.Venue == 'SUBWAY')]
    
    return(nearby_venues)

#### Pull Foursquare data for Selected Neighborhoods

In [149]:
# Loop thru neighborhoods selected to get venue data
select_venues = getNearbyFFVenues(names=Select_neighborhoods['Neighborhood'],
                                   latitudes=Select_neighborhoods['LAT'],
                                   longitudes=Select_neighborhoods['LONG'])


SHARPSTOWN
BRAEBURN
GULFTON
MEYERLAND AREA


#### Confirm a limited sample size 

In [150]:
select_venues.shape

(19, 8)

In [151]:
# Select a neighborhood to examine from cluster results
select_venues.head(10)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
15    SHARPSTOWN              29.703853              -95.524952   
40    SHARPSTOWN              29.703853              -95.524952   
50    SHARPSTOWN              29.703853              -95.524952   
62    SHARPSTOWN              29.703853              -95.524952   
84    SHARPSTOWN              29.703853              -95.524952   
91    SHARPSTOWN              29.703853              -95.524952   
123     BRAEBURN              29.681566              -95.515667   
136     BRAEBURN              29.681566              -95.515667   
150     BRAEBURN              29.681566              -95.515667   
151     BRAEBURN              29.681566              -95.515667   

                     Venue ID            Venue  Venue Latitude  \
15   5cd2643147f876002c912810      Whataburger       29.699264   
40   4baa8adcf964a52020733ae3  Churchs Chicken       29.713848   
50   4bd9ef0cc79cc92837b37ce9           SUBWAY       29.704174   
62   4cf925c501568cfa61a224e7  Churchs Chicken       29.692005   
84   4b70dca3f964a52012322de3      Burger King       29.717177   
91   4e442820d22de4060ef24256        McDonalds       29.690223   
123  5cd2643147f876002c912810      Whataburger       29.699264   
136  4e4d05aebd413c4cc66e0e0a           SUBWAY       29.672400   
150  4e7376e9e4cd876b6e111003           SUBWAY       29.674390   
151  4cf925c501568cfa61a224e7  Churchs Chicken       29.692005   

     Venue Longitude        Venue Category  
15        -95.517862          Burger Joint  
40        -95.539402   Fried Chicken Joint  
50        -95.514355        Sandwich Place  
62        -95.528487   Fried Chicken Joint  
84        -95.538614  Fast Food Restaurant  
91        -95.534942  Fast Food Restaurant  
123       -95.517862          Burger Joint  
136       -95.508812        Sandwich Place  
150       -95.531759        Sandwich Place  
151       -95.528487   Fried Chicken Joint

### 4D - Get Ratings for selected Fast Food Venues

#### Send GET request for result for venue ratings and likes

In [155]:
def getVenueRatings(venue_ids):
    
    #RUN FIRST TIME ONLY
    ratingsdf1 = pd.DataFrame(columns=['Venue ID','Venue', 'Rating', 'Likes'])

    
    for venue_id in venue_ids:
        print(venue_id)
        url2 = 'https://api.foursquare.com/v2/venues/{}?client_id={}&client_secret={}&v={}'.format(
            venue_id,
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION)

        result = requests.get(url2).json()
    
        test_ratings=[]
        # return only relevant information for each nearby venue
        test_ratings.append(venue_id)
        test_ratings.append(result['response']['venue']['name'])
        test_ratings.append(result['response']['venue']['rating'])
        test_ratings.append(result['response']['venue']['likes']['count'])

        #test_ratings  
        
        ratingsdf1 = ratingsdf1.append({'Venue ID':test_ratings[0],'Venue': test_ratings[1], 'Rating': test_ratings[2], 'Likes': test_ratings[3]}, ignore_index=True)

        #ratingsdf1

    return(ratingsdf1)

In [157]:
# Loop thru venues selected to get rating data
rated_venues = getVenueRatings(venue_ids=select_venues['Venue ID'])
                                   


5cd2643147f876002c912810
4baa8adcf964a52020733ae3
4bd9ef0cc79cc92837b37ce9
4cf925c501568cfa61a224e7
4b70dca3f964a52012322de3
4e442820d22de4060ef24256
5cd2643147f876002c912810
4e4d05aebd413c4cc66e0e0a
4e7376e9e4cd876b6e111003
4cf925c501568cfa61a224e7
4be85b1688ed2d7f0fc5cb1d
4b967a62f964a520b6ce34e3
4ba8f96af964a52098ff39e3
4c19404d838020a1df6ee561
4b522c57f964a5205e6d27e3
4c4c8fa0712ac928003d836e
4c3de9f383a3a593ac51ed33
5787b572498e5eaf0057388b
4d7bd1bb7498a1cd7ec871fc


Double check ratings and venues dataframe before merging
keep dataframe listings commented out

In [158]:
rated_venues = rated_venues[['Venue ID', 'Rating', 'Likes']]
#rated_venues

In [159]:
ff_venues = select_venues.reset_index(drop=True)
#ff_venues

Create final merged rating dataset with Neighborhood, Venue, Ratins, and Likes 

In [160]:
#venue_rating = pd.merge(ff_venues, rated_venues, on='Venue ID', how='outer')
venue_rating1 = pd.concat([ff_venues, rated_venues], axis=1, sort=False)

#ff_venues.merge(rated_venues) 

In [161]:
#venue_rating
#venue_rating1
venue_rating1.rename(columns={'Venue ID':'VID'}, inplace=True)

venue_rating1.drop(['Neighborhood Latitude', 'Neighborhood Longitude', 'VID', 'Venue Category', 'Venue Latitude', 'Venue Longitude'], axis=1, inplace=True)
#select_venues
#rated_venues
#ff_venues.dtypes
venue_rating1


Neighborhood            Venue  Rating Likes
0       SHARPSTOWN      Whataburger     7.4     2
1       SHARPSTOWN  Churchs Chicken     7.3     9
2       SHARPSTOWN           SUBWAY     6.6     9
3       SHARPSTOWN  Churchs Chicken     6.6     3
4       SHARPSTOWN      Burger King     6.2     6
5       SHARPSTOWN        McDonalds     5.6     8
6         BRAEBURN      Whataburger     7.4     2
7         BRAEBURN           SUBWAY     6.6     0
8         BRAEBURN           SUBWAY     6.6     0
9         BRAEBURN  Churchs Chicken     6.6     3
10        BRAEBURN           SUBWAY     6.3     3
11         GULFTON      Whataburger     8.1    32
12         GULFTON           SUBWAY     6.8     2
13         GULFTON  Jack in the Box     7.1     8
14  MEYERLAND AREA      Whataburger     7.8    47
15  MEYERLAND AREA  Jack in the Box     7.2     7
16  MEYERLAND AREA           SUBWAY     6.3     5
17  MEYERLAND AREA        McDonalds     6.7     8
18  MEYERLAND AREA           SUBWAY     6.6     0

### 4E - Create sorted Prints of Ratings Data 

#### Selected fast food venues grouped by neighborhood.
Use to find unusually low rated restaurant relative to other restaurants in Neighborhood

In [162]:
NBHOODgrouped_df = venue_rating1.groupby('Neighborhood')
print('SELECTED FAST FOOD RESAURANTS GROUPED BY NEIGHBORHOOD SORTED BY RATING')
for key, item in NBHOODgrouped_df:
    print(NBHOODgrouped_df.get_group(key), "\n\n")

SELECTED FAST FOOD RESAURANTS GROUPED BY NEIGHBORHOOD SORTED BY RATING
   Neighborhood            Venue  Rating Likes
6      BRAEBURN      Whataburger     7.4     2
7      BRAEBURN           SUBWAY     6.6     0
8      BRAEBURN           SUBWAY     6.6     0
9      BRAEBURN  Churchs Chicken     6.6     3
10     BRAEBURN           SUBWAY     6.3     3 


   Neighborhood            Venue  Rating Likes
11      GULFTON      Whataburger     8.1    32
12      GULFTON           SUBWAY     6.8     2
13      GULFTON  Jack in the Box     7.1     8 


      Neighborhood            Venue  Rating Likes
14  MEYERLAND AREA      Whataburger     7.8    47
15  MEYERLAND AREA  Jack in the Box     7.2     7
16  MEYERLAND AREA           SUBWAY     6.3     5
17  MEYERLAND AREA        McDonalds     6.7     8
18  MEYERLAND AREA           SUBWAY     6.6     0 


  Neighborhood            Venue  Rating Likes
0   SHARPSTOWN      Whataburger     7.4     2
1   SHARPSTOWN  Churchs Chicken     7.3     9
2   SHARPSTO

#### Selected fast food venues grouped by fast food franchise.
Use to find unusually low rated restaurant relative to similar franchises across similar neighborhoods

In [163]:
Vengrouped_df = venue_rating1.groupby('Venue')
print('SELECTED FAST FOOD RESAURANTS GROUPED BY FRANCHISE SORTED BY RATING')
for key, item in Vengrouped_df:
    print(Vengrouped_df.get_group(key).sort_values(['Rating'],ascending=False), "\n\n")
    
#days_off_yearly = venue_rating1.groupby(["Venue", "Rating"]).agg({"out_days": [np.sum]})    
#print (venue_rating1.reset_index()
#                      .sort_values(['from_year','out_days'],ascending=False)
#                      .set_index(['from_year','name']))


SELECTED FAST FOOD RESAURANTS GROUPED BY FRANCHISE SORTED BY RATING
  Neighborhood        Venue  Rating Likes
4   SHARPSTOWN  Burger King     6.2     6 


  Neighborhood            Venue  Rating Likes
1   SHARPSTOWN  Churchs Chicken     7.3     9
3   SHARPSTOWN  Churchs Chicken     6.6     3
9     BRAEBURN  Churchs Chicken     6.6     3 


      Neighborhood            Venue  Rating Likes
15  MEYERLAND AREA  Jack in the Box     7.2     7
13         GULFTON  Jack in the Box     7.1     8 


      Neighborhood      Venue  Rating Likes
17  MEYERLAND AREA  McDonalds     6.7     8
5       SHARPSTOWN  McDonalds     5.6     8 


      Neighborhood   Venue  Rating Likes
12         GULFTON  SUBWAY     6.8     2
2       SHARPSTOWN  SUBWAY     6.6     9
7         BRAEBURN  SUBWAY     6.6     0
8         BRAEBURN  SUBWAY     6.6     0
18  MEYERLAND AREA  SUBWAY     6.6     0
10        BRAEBURN  SUBWAY     6.3     3
16  MEYERLAND AREA  SUBWAY     6.3     5 


      Neighborhood        Venue  Rating

### **CONCLUSIONS**

My key conclusions are as follows:

1) Only the McDonalds in Sharpstown was significantlly lowest rated both for all fast food restaurants in Sharpstown and similar Neighborhoods analyzed and lowest rated of McDonalds. This venue should be on your list of underperformers 
    
2) Most restaurants had very similar ratings and no other venues stood out as low rated in our select area

3) Whataburger stands out as best overall rated restaurant. Consider a New Whataburger in a Neighborhood lacking Whataburger. 
 
4) The "Likes" information was only useful in a qualitative sense and best identified the most popular indiviual restaurants such as the Whataburgers in Gulfton and Meyerland.
    
I did not analyze venue ratings for the entire City or larger area because of the issue with foursquare limiting the ratings data as a premium servide. With a paying account more might be done.
      
Identifying  lower rated restaurants would allow the investor to build a list a restaurants to begin looking into further deetail to pursue for purchase. With Whataburgers being noticeably higher rated, it might be better to start new.

### About this notebook
This notebook was created as final capstone project in IBM Data Science Professional Certificate course

An original notebook  created by [Alex Aklson](https://www.linkedin.com/in/aklson/) was used as the goby and customized for this assignment